In [1]:
from theano.sandbox import cuda
cuda.use('gpu0')
import os, sys
%cd /home/von/bb/fastai/private/dogsvcatsredux/
current_dir = os.getcwd()


Using gpu device 0: GeForce GTX 1070 (CNMeM is disabled, cuDNN 5103)
/usr/lib/python2.7/site-packages/theano/sandbox/cuda/__init__.py:600: UserWarning: Your cuDNN version is more recent than the one Theano officially supports. If you see any problems, try updating Theano or downgrading cuDNN to version 5.
  warnings.warn(warn)


/home/von/bb/fastai/private/dogsvcatsredux


In [2]:
%matplotlib inline
import os, sys
from __future__ import division, print_function
import math
LESSON_HOME_DIR = current_dir
DATA_HOME_DIR = current_dir+'/data/dogscatsredux'
#Allow relative imports to directories above lesson1/
sys.path.insert(1, os.path.join(sys.path[0], '..'))
#import modules
import utils; reload(utils)
from utils import *
import vgg16
import vgg16bn


%cd $DATA_HOME_DIR

#Set path to sample/ path if desired
path = DATA_HOME_DIR + '/' #'/sample/'
test_path = DATA_HOME_DIR + '/test/' #We use all the test data
results_path=DATA_HOME_DIR + '/results/'
model_path=DATA_HOME_DIR + '/models/'
train_path=path + '/train/'
valid_path=path + '/valid/'
print(os.getcwd())

batch_size=48
no_of_epochs=10


/home/von/bb/fastai/private/dogsvcatsredux/data/dogscatsredux
/home/von/bb/fastai/private/dogsvcatsredux/data/dogscatsredux


Using Theano backend.


## Setup

In [3]:
batches = get_batches(path+'train', shuffle=False, batch_size=batch_size)
val_batches = get_batches(path+'valid', shuffle=False, batch_size=batch_size)

Found 23000 images belonging to 2 classes.
Found 2000 images belonging to 2 classes.


In [4]:
(val_classes, trn_classes, val_labels, trn_labels, 
    val_filenames, filenames, test_filenames) = get_classes(path)

Found 23000 images belonging to 2 classes.
Found 2000 images belonging to 2 classes.
Found 12500 images belonging to 1 classes.


In this notebook we're going to create an ensemble of models and use their average as our predictions. For each ensemble, we're going to follow our usual fine-tuning steps:

1) Create a model that retrains just the last layer
2) Add this to a model containing all VGG layers except the last layer
3) Fine-tune just the dense layers of this model (pre-computing the convolutional layers)
4) Add data augmentation, fine-tuning the dense layers without pre-computation.

So first, we need to create our VGG model and pre-compute the output of the conv layers:

In [22]:
model = Vgg16BN().model
conv_layers,fc_layers = split_at(model, Convolution2D)

/usr/lib/python2.7/site-packages/keras/layers/core.py:577: UserWarning: `output_shape` argument not specified for layer lambda_5 and cannot be automatically inferred with the Theano backend. Defaulting to output shape `(None, 3, 224, 224)` (same as input shape). If the expected output shape is different, specify it via the `output_shape` argument.
  .format(self.name, input_shape))


using updated version


In [23]:
conv_model = Sequential(conv_layers)

In [24]:
#val_features = conv_model.predict_generator(val_batches, val_batches.nb_sample)
#trn_features = conv_model.predict_generator(batches, batches.nb_sample)
val_features = load_array('val_conv')
trn_features = load_array('train_conv')

In [33]:
save_array(model_path + 'train_convlayer_features.bc', trn_features)
save_array(model_path + 'valid_convlayer_features.bc', val_features)

In the future we can just load these precomputed features:

In [6]:
trn_features = load_array(model_path+'train_convlayer_features.bc')
val_features = load_array(model_path+'valid_convlayer_features.bc')

We can also save some time by pre-computing the training and validation arrays with the image decoding and resizing already done:

In [9]:
trn = get_data(path+'train')
val = get_data(path+'valid')

Found 23000 images belonging to 2 classes.


MemoryError: 

In [8]:
save_array(model_path+'train_data.bc', trn)
save_array(model_path+'valid_data.bc', val)

In the future we can just load these resized images:

In [7]:
trn = load_array(model_path+'train_data.bc')
val = load_array(model_path+'valid_data.bc')

In [15]:
trn = batches
val = val_batches

Finally, we can precompute the output of all but the last dropout and dense layers, for creating the first stage of the model:

In [8]:
model.pop()
model.pop()

In [9]:
ll_val_feat = model.predict_generator(val_batches, val_batches.nb_sample)
ll_feat = model.predict_generator(batches, batches.nb_sample)

In [10]:
save_array(model_path + 'train_ll_feat.bc', ll_feat)
save_array(model_path + 'valid_ll_feat.bc', ll_val_feat)

In [8]:
ll_feat = load_array(model_path+ 'train_ll_feat.bc')
ll_val_feat = load_array(model_path + 'valid_ll_feat.bc')

...and let's also grab the test data, for when we need to submit:

In [16]:
test = get_data(path+'test')
save_array(model_path+'test_data.bc', test)

Found 12500 images belonging to 1 classes.


In [22]:
test = load_array(model_path+'test_data.bc')

## Last layer

The functions automate creating a model that trains the last layer from scratch, and then adds those new layers on to the main model.

In [11]:
def get_ll_layers():
    return [ 
        BatchNormalization(input_shape=(4096,)),
        Dropout(0.5),
        Dense(2, activation='softmax') 
        ]

In [26]:
def train_last_layer(i):
    ll_layers = get_ll_layers()
    ll_model = Sequential(ll_layers)
    ll_model.compile(optimizer=Adam(), loss='categorical_crossentropy', metrics=['accuracy'])
    ll_model.optimizer.lr=1e-5
    ll_model.fit(ll_feat, trn_labels, validation_data=(ll_val_feat, val_labels), nb_epoch=12)
    ll_model.optimizer.lr=1e-7
    ll_model.fit(ll_feat, trn_labels, validation_data=(ll_val_feat, val_labels), nb_epoch=1)
    ll_model.save_weights(model_path+'ll_bn' + i + '.h5')

    vgg = Vgg16BN()
    model = vgg.model
    model.pop(); model.pop(); model.pop()
    for layer in model.layers: layer.trainable=False
    model.compile(optimizer=Adam(), loss='categorical_crossentropy', metrics=['accuracy'])

    ll_layers = get_ll_layers()
    for layer in ll_layers: model.add(layer)
    for l1,l2 in zip(ll_model.layers, model.layers[-3:]):
        l2.set_weights(l1.get_weights())
    model.compile(optimizer=Adam(), loss='categorical_crossentropy', metrics=['accuracy'])
    model.save_weights(model_path+'bn' + i + '.h5')
    return model

## Dense model

In [13]:
def get_conv_model(model):
    layers = model.layers
    last_conv_idx = [index for index,layer in enumerate(layers) 
                         if type(layer) is Convolution2D][-1]

    conv_layers = layers[:last_conv_idx+1]
    conv_model = Sequential(conv_layers)
    fc_layers = layers[last_conv_idx+1:]
    return conv_model, fc_layers, last_conv_idx

In [14]:
def get_fc_layers(p, in_shape):
    return [
        MaxPooling2D(input_shape=in_shape),
        Flatten(),
        Dense(4096, activation='relu'),
        BatchNormalization(),
        Dropout(p),
        Dense(4096, activation='relu'),
        BatchNormalization(),
        Dropout(p),
        Dense(2, activation='softmax')
        ]

In [36]:
def train_dense_layers(i, model):
    gen = image.ImageDataGenerator(rotation_range=10, width_shift_range=0.05, 
       zoom_range=0.05,
       channel_shift_range=10, height_shift_range=0.05, shear_range=0.05, horizontal_flip=True) 
    val_batches = get_batches(valid_path, shuffle=False, batch_size=batch_size)
    batches = get_batches(train_path, gen, shuffle=True, batch_size=batch_size)

    conv_model, fc_layers, last_conv_idx = get_conv_model(model)
    conv_shape = conv_model.output_shape[1:]
    fc_model = Sequential(get_fc_layers(0.5, conv_shape))
    fc_model.summary()
    print(fc_layers)

    for l1,l2 in zip(fc_model.layers, fc_layers): 
        weights = l2.get_weights()
        l1.set_weights(weights)
    fc_model.compile(optimizer=Adam(1e-5), loss='categorical_crossentropy', 
                     metrics=['accuracy'])
    fc_model.fit(trn_features, trn_labels, nb_epoch=2, 
         batch_size=batch_size, validation_data=(val_features, val_labels))

   

    for layer in conv_model.layers: layer.trainable = False
    for layer in get_fc_layers(0.5, conv_shape): conv_model.add(layer)
    for l1,l2 in zip(conv_model.layers[last_conv_idx+1:], fc_model.layers): 
        l1.set_weights(l2.get_weights())

    conv_model.compile(optimizer=Adam(1e-5), loss='categorical_crossentropy', 
                       metrics=['accuracy'])
    conv_model.save_weights(model_path+'no_dropout_bn' + i + '.h5')
    conv_model.fit_generator(batches, samples_per_epoch=batches.N, nb_epoch=1, 
                            validation_data=val_batches, nb_val_samples=val_batches.N)
    for layer in conv_model.layers[16:]: layer.trainable = True
    conv_model.fit_generator(batches, samples_per_epoch=batches.N, nb_epoch=8, 
                            validation_data=val_batches, nb_val_samples=val_batches.N)

    conv_model.optimizer.lr = 1e-7
    conv_model.fit_generator(batches, samples_per_epoch=batches.N, nb_epoch=10, 
                            validation_data=val_batches, nb_val_samples=val_batches.N)
    conv_model.save_weights(model_path + 'aug' + i + '.h5')

## Build ensemble

In [37]:
for i in range(5):
    i = str(i)
    model = train_last_layer(i)
    train_dense_layers(i, model)

Train on 23000 samples, validate on 2000 samples
Epoch 1/12
23000/23000 [==============================] - 1s - loss: 0.7182 - acc: 0.7143 - val_loss: 0.1662 - val_acc: 0.9365

/usr/lib/python2.7/site-packages/keras/layers/core.py:577: UserWarning: `output_shape` argument not specified for layer lambda_10 and cannot be automatically inferred with the Theano backend. Defaulting to output shape `(None, 3, 224, 224)` (same as input shape). If the expected output shape is different, specify it via the `output_shape` argument.
  .format(self.name, input_shape))


using updated version
Found 2000 images belonging to 2 classes.
Found 23000 images belonging to 2 classes.
____________________________________________________________________________________________________
Layer (type)                     Output Shape          Param #     Connected to                     
maxpooling2d_56 (MaxPooling2D)   (None, 512, 7, 7)     0           maxpooling2d_input_6[0][0]       
____________________________________________________________________________________________________
flatten_16 (Flatten)             (None, 25088)         0           maxpooling2d_56[0][0]            
____________________________________________________________________________________________________
dense_62 (Dense)                 (None, 4096)          102764544   flatten_16[0][0]                 
____________________________________________________________________________________________________
batchnormalization_37 (BatchNorm (None, 4096)          16384       dense_62[0][0]    

/usr/lib/python2.7/site-packages/keras/layers/core.py:577: UserWarning: `output_shape` argument not specified for layer lambda_11 and cannot be automatically inferred with the Theano backend. Defaulting to output shape `(None, 3, 224, 224)` (same as input shape). If the expected output shape is different, specify it via the `output_shape` argument.
  .format(self.name, input_shape))


using updated version
Found 2000 images belonging to 2 classes.
Found 23000 images belonging to 2 classes.
____________________________________________________________________________________________________
Layer (type)                     Output Shape          Param #     Connected to                     
maxpooling2d_63 (MaxPooling2D)   (None, 512, 7, 7)     0           maxpooling2d_input_7[0][0]       
____________________________________________________________________________________________________
flatten_19 (Flatten)             (None, 25088)         0           maxpooling2d_63[0][0]            
____________________________________________________________________________________________________
dense_73 (Dense)                 (None, 4096)          102764544   flatten_19[0][0]                 
____________________________________________________________________________________________________
batchnormalization_45 (BatchNorm (None, 4096)          16384       dense_73[0][0]    

...

using updated version
Found 2000 images belonging to 2 classes.
Found 23000 images belonging to 2 classes.
____________________________________________________________________________________________________
Layer (type)                     Output Shape          Param #     Connected to                     
maxpooling2d_70 (MaxPooling2D)   (None, 512, 7, 7)     0           maxpooling2d_input_8[0][0]       
____________________________________________________________________________________________________
flatten_22 (Flatten)             (None, 25088)         0           maxpooling2d_70[0][0]            
____________________________________________________________________________________________________
dense_84 (Dense)                 (None, 4096)          102764544   flatten_22[0][0]                 
____________________________________________________________________________________________________
batchnormalization_53 (BatchNorm (None, 4096)          16384       dense_84[0][0]    

/usr/lib/python2.7/site-packages/keras/layers/core.py:577: UserWarning: `output_shape` argument not specified for layer lambda_13 and cannot be automatically inferred with the Theano backend. Defaulting to output shape `(None, 3, 224, 224)` (same as input shape). If the expected output shape is different, specify it via the `output_shape` argument.
  .format(self.name, input_shape))


using updated version
Found 2000 images belonging to 2 classes.
Found 23000 images belonging to 2 classes.
____________________________________________________________________________________________________
Layer (type)                     Output Shape          Param #     Connected to                     
maxpooling2d_77 (MaxPooling2D)   (None, 512, 7, 7)     0           maxpooling2d_input_9[0][0]       
____________________________________________________________________________________________________
flatten_25 (Flatten)             (None, 25088)         0           maxpooling2d_77[0][0]            
____________________________________________________________________________________________________
dense_95 (Dense)                 (None, 4096)          102764544   flatten_25[0][0]                 
____________________________________________________________________________________________________
batchnormalization_61 (BatchNorm (None, 4096)          16384       dense_95[0][0]    

/usr/lib/python2.7/site-packages/keras/layers/core.py:577: UserWarning: `output_shape` argument not specified for layer lambda_14 and cannot be automatically inferred with the Theano backend. Defaulting to output shape `(None, 3, 224, 224)` (same as input shape). If the expected output shape is different, specify it via the `output_shape` argument.
  .format(self.name, input_shape))


using updated version
Found 2000 images belonging to 2 classes.
Found 23000 images belonging to 2 classes.
____________________________________________________________________________________________________
Layer (type)                     Output Shape          Param #     Connected to                     
maxpooling2d_84 (MaxPooling2D)   (None, 512, 7, 7)     0           maxpooling2d_input_10[0][0]      
____________________________________________________________________________________________________
flatten_28 (Flatten)             (None, 25088)         0           maxpooling2d_84[0][0]            
____________________________________________________________________________________________________
dense_106 (Dense)                (None, 4096)          102764544   flatten_28[0][0]                 
____________________________________________________________________________________________________
batchnormalization_69 (BatchNorm (None, 4096)          16384       dense_106[0][0]   

## Combine ensemble and test

In [38]:
ens_model = vgg_ft(2)
for layer in ens_model.layers: layer.trainable=True

/usr/lib/python2.7/site-packages/keras/layers/core.py:577: UserWarning: `output_shape` argument not specified for layer lambda_15 and cannot be automatically inferred with the Theano backend. Defaulting to output shape `(None, 3, 224, 224)` (same as input shape). If the expected output shape is different, specify it via the `output_shape` argument.
  .format(self.name, input_shape))


In [39]:
def get_ens_pred(arr, fname):
    ens_pred = []
    for i in range(5):
        i = str(i)
        ens_model.load_weights('{}{}{}.h5'.format(model_path, fname, i))
        preds = ens_model.predict(arr, batch_size=batch_size)
        ens_pred.append(preds)
    return ens_pred

In [40]:
val_pred2 = get_ens_pred(val, 'aug')

ValueError: You are trying to load a weight file containing 18 layers into a model with 16 layers.

In [56]:
val_avg_preds2 = np.stack(val_pred2).mean(axis=0)

In [61]:
categorical_accuracy(val_labels, val_avg_preds2).eval()

array(0.9894999861717224, dtype=float32)

In [29]:
gen = image.ImageDataGenerator(rotation_range=10, width_shift_range=0.05, 
       zoom_range=0.05,
       channel_shift_range=10, height_shift_range=0.05, shear_range=0.05, horizontal_flip=True)